# バイナリ整数線形計画問題

## 概要

$\mathbf{x} = (x_1, x_2, \dots, x_N)$のように、$N$個の$\{ 0, 1\}$バイナリ変数列をひとまとめにしたベクトルがあります。バイナリ整数線形計画(integer linear programming; ILP)問題とは

$$S \mathbf{x} = \mathbf{b} \tag{1}$$

という制約を満たしつつ、あるベクトル$\mathbf{c}$に対して

$$\mathbf{c} \cdot \mathbf{x} \tag{2}$$

を最大化するような$\mathbf{x}$を求める問題です。ここで$S$は$M \times N$の行列、$\mathbf{b}$は$M$個の成分を持つベクトルです。

この問題はNP困難であることが知られています。またこのような解が存在するかどうかを判定する決定問題ではNP完全となります。

## 応用例: 資本予算問題 (Capital Budgeting)

あなたはベンチャーキャピタルに勤めています。いくつかのベンチャー企業を投資候補とし、その中から投資先を決定します。この投資はベンチャーの成長を見守るという観点から、少額の部分的な投資を行っても意味がありません。このときどのように投資する・しないを決定すれば、投資先のベンチャーからのリターンを最大化できるでしょうか。

この場合、0または1で投資する・しないを表現することができるという類似性から、資本予算問題はバイナリ整数線形計画問題として考えることができます。

## 応用例: 倉庫配置問題 (Warehouse Location)

あなたはある流通会社のマネージャーです。ある商品に対する$M$人の顧客の需要を満たすために、$N$個の倉庫のうちのどれを用いるかを決定する必要があります。よって、あなたはどの倉庫を運営し、どの倉庫からどの顧客にどれだけ出荷するかを考える必要があるでしょう。需要を満たすために倉庫を運営する・しないを0・1で決定すれば、これも立派な組合せ最適化問題です。また$i$番目の倉庫から$j$番目の顧客に送る荷物の量を$x_{ij}$、$j$番目の顧客に必要な荷物の量を$d_j$とすれば

$$\sum_{i=1}^N x_{ij} = d_j$$

のような制約が生まれます。これは(1)式と同じ形であることから、この問題もバイナリ整数線形計画問題として定式化されます。

今回は様々な応用例が考えられるバイナリ整数線形計画問題を例に、JijModelingおよびJijZeptの使い方を見ていきましょう。

# 数理モデル

## バイナリ変数

概要で述べたように$x_j=\{0, 1\}$のようなバイナリ変数を$N$個用意します。

## 制約: 連立線形方程式を満たさなければならない

(1)式を満たす必要があるため、これを$i, j$の添字を用いてあらわに書くと

$$\sum_{j=1}^N S_{ij} x_j = b_i \quad (\forall i)\tag{3}$$

のようになります。

## 目的関数

今、最大化したいのは(2)式です。よってこちらも添字を使ってあらわに書くと

$$\mathrm{obj} = - \sum_{j=1}^N c_j x_j \tag{4}$$

となります。マイナスをつけることで、最小値を求める数理最適化問題を、最大値を求める問題に変換しています。

# 実装しましょう

それでは実際に、Jijのプロダクトを用いてバイナリ整数線形計画問題を解くためのPythonスクリプトを作成しましょう。

## JijModelingで問題の作成

`JijModeling`を用いて問題の作成を行います。

### 作成・初期化

以下のようにして問題を初期化します。

In [1]:
import jijmodeling as jm

# set problem
problem = jm.Problem('binary_ilp')

### 変数の定義

次にこの問題で用いる種々の変数を定義しましょう。

In [2]:
# define variables
S = jm.Placeholder('S', dim=2)
M = S.shape[0]
N = S.shape[1]
b = jm.Placeholder('b', shape=(M))
c = jm.Placeholder('c', shape=(N))
x = jm.Binary('x', shape=(N))
i = jm.Element('i', M)
j = jm.Element('j', N)

`S`は行列$S$、`M`は行列$S$の行数、`N`は行列$S$の列数です。`b`, `c`はそれぞれ$\mathbf{b}, \mathbf{c}$を表し、`x`は$\{ 0, 1\}$のバイナリ変数列です。  
ここでは`S`の大きさを明示的に記述せず、2次元リストであることだけ(`dim=2`)を入力しています。そして`S`が`M`行`N`列という形であることから、`b`, `c`, `x`の形を定義するのに必要な要素数を`shape`を用いて抽出しています。  

> このように書くことで、`S`の行数・列数の変更に伴うスクリプトの改訂作業は、後にご紹介するインスタンス作成部分だけで済みます。

最後に、この最適化問題で用いる添字`i`, `j`を定義しています。このように定義すると、例えば添字`i`は$i=0, 1, \dots, M-1$の範囲を取り得ることを意味します。

### 制約の実装

数理モデルである(3)式を`JijModeling`で表現しましょう。

In [3]:
# set constraint
const = jm.Sum(j, S[i, j]*x[j]) - b[i]
problem += jm.Constraint('h1', const==0, forall=i)

`JijModeling`の`Sum`を用いることで総和を表現します。`j`は総和の添字を表しており、`jm.Sum`部分は$j=0, 1, \dots, N-1$の和を取ることを意味します。そして`Constraint`を用いて、`h1`という名前でこの制約を登録しています。このとき、(3)式の「全てのiに対して」という条件を加えるには、`forall=i`のように記述します。最後に、ここで定義した制約を`problem`に挿入しています。

> JijModeling 0.9.0 より以前のバージョンでは、`jm.Sum({'j': N}, S['i', 'j']*x['j'])`のように総和を取る添字に文字列を用いることができました。しかし、記述ミスを増やしてしまう問題があったため、最新のバージョンでは使えなくなっています。ご注意ください。

### 目的関数の実装

同様に、目的関数(4)式も実装します。

In [4]:
# set objective function
obj = - jm.Sum(j, c[j]*x[j])
problem += obj

ここで、これまで定義してきた問題が正しく実装されているかを見てみましょう。Jupyter Notebookであれば作成した数式を表示することができるため、実装が正しくされているかを即座に確認することができます。

In [5]:
problem

## インスタンスの作成

ここまでは数式をスクリプトに落とし込む作業をしただけで、行列$S$の値や$\mathbf{b}, \mathbf{c}$の値およびその要素数などを具体的に与えてきませんでした。ここで実際に解きたい問題の数値を吹き込みます。

In [6]:
# set S matrix
inst_S = [[0, 2, 0, 2, 0], [1, 0, 1, 0, 1], [1, 2, 3, 2, 1]]
# set b vector
inst_b = [2, 2, 6]
# set c vector
inst_c = [1, 2, 3, 4, 5]
instance_data = {'S': inst_S, 'b': inst_b, 'c': inst_c}

先ほど定義した`S=jm.PlaceholderArray('S', dim=2)`, `b = jm.PlaceholderArray('b', shape=(M))`, `c = jm.PlaceholderArray('c', shape=(N))`に実際に入れるリストを与えます。ここでは

$$S = \left( \begin{array}{ccccc}
0 & 2 & 0 & 2 & 0 \\
1 & 0 & 1 & 0 & 1 \\
1 & 2 & 3 & 2 & 1 
\end{array}\right), \quad 
\mathbf{b} = \left( \begin{array}{c}
2 \\
2 \\
6 
\end{array}\right), \quad 
\mathbf{c} = \left( \begin{array}{c}
1 \\
2 \\
3 \\
4 \\
5 
\end{array}\right)$$

と設定しています。

もしこれらの行列・ベクトルの行数・列数を変更する場合でも、先ほど実装した問題作成部分を変更する必要はありません。これは先ほどの実装が`JijModeling`を用いた抽象度の高い実装になっているためです(問題作成部分には具体的な数値が何一つ現れていないことから、それがわかります)。  
最後に`JijZept`でこの問題を解くために、これらの情報を辞書型に格納しています。

## 未定乗数の決定

制約をどの程度の重みで満たさなければならないか、その度合いを表す未定乗数を設定します。ここでは$\lambda_1 = 2.0$としています。

In [17]:
# set multipliers
lam1 = 2.0
multipliers = {'h1': lam1}

先ほど`Constraint('h1', const)`のようにして名付けた制約に対応する未定乗数の値を、辞書型で設定します。

## JijZeptで問題を解く

それでは`JijZept`のSAを用いて、この問題の最適解を求めましょう。

In [18]:
import jijzept as jz

# set sampler
sampler = jz.JijSASampler(config='./config.toml')
# solve problem
response = sampler.sample_model(problem, instance_data, multipliers)

uploading instance ...
submitting query ...
submitted to the queue.
Your solution_id is fe9712c13ffa4d39b90c1e47c8d52540.


`JijZept`の`JijSASampler`を用います。このとき`config.toml`に必要な情報を入力し、これを読み込みます。  
`sampler.sample_model()`に先程までで実装してきた`problem`、そして実際の値を持つ`instance_data`と、制約の未定乗数`multipliers`を入力することで、実際に数値を当てはめた問題を未定乗数を指定して解きます。

## 解析しやすくする

出てきた結果である`response`を見てみましょう。

In [19]:
response

<APIStatus.SUCCESS: 'SUCCESS'>
DimodResponse(rec.array([([0, 0, 1, 1, 1], -56., 1)],
          dtype=[('sample', 'i1', (5,)), ('energy', '<f8'), ('num_occurrences', '<i8')]), Variables(['x[0]', 'x[1]', 'x[2]', 'x[3]', 'x[4]']), {'sampling_time': 269.50519531965256}, 'BINARY')

情報が羅列されていることがわかります。このままでは出てきた結果を解析することが困難です。よって解析や解の可視化を行いやすくするために、decode作業を行いましょう。

In [20]:
# decode solution
decoded = problem.decode(response, instance_data, {})

このdecode作業には「元の問題がどのようなものであったか」という情報が必要なため、`problem.decode`に`instance_data`を入力することで達成されます。  
それでは`decoded`の中身を見てみましょう。

In [21]:
print(decoded.solutions)
print(decoded.objectives)
print(decoded.constraint_expr_value)
print(decoded.constraint_violations)

[{'x': array([0., 0., 1., 1., 1.])}]
[-12.]
[{'h1': {(0,): 0.0, (1,): 0.0, (2,): 0.0}}]
[{'h1': 0.0}]


`decoded.solutions`にはその解を構成するバイナリ変数の並び、`decoded.objective`には目的関数の値、`decoded.constraint_expr_value`には制約項の期待値からのズレ(全て0であれば制約が満たされている)、そして`decoded.constraint_violation`には合計で制約がどれだけ敗れているかがそれぞれ格納されています。ここから$\mathbf{x}=(0, 0, 1, 1, 1)$が解として選ばれ、このとき$H_1=0, \ \mathrm{obj}=-12$であることがわかりました。

$H_1=0$を満たす解(実行可能解)としては他に$(1, 1, 1, 0, 0)$などがあります。しかし$\mathbf{c}$の値から、$\mathbf{c}\cdot \mathbf{x}$が最大となるものが発見されていることがわかります。

# 結言

今回は資本予算問題などの重要な最適化問題の基礎となっているバイナリ整数線形計画問題を例に、JijModelingとJijZeptの使い方をご紹介しました。以下に今回登場したテクニックや注意点をまとめます。

- JijModelingの`Sum(添字, 和を取る数式)`を用いることで簡単に総和を記述することができる。ただし添字はあらかじめ`Element`として定義しておかなければならない。
- `Constraint`を用いることで、制約項を定義する。このとき、その制約には好きな名前をつけることができる。
- `Constraint`が$\forall i$のように複数の式を表す場合、`forall`を用いて添字の範囲・条件を指定することができる。
- `Constraint`で名付けた制約の名前に対応する未定乗数を辞書型で設定する。
- JijModelingを用いた抽象度の高い実装を行うことで、インスタンス変更が容易にできる柔軟性の高いスクリプトを構築することができる。
- インスタンス・未定乗数の情報は辞書型にまとめ、後ほどJijZeptのサンプラーに渡す。
- 解いた結果である`response`は解析を行うには不明な点が多いため、decode作業を行う。これにより、アニーリングで得られたバイナリ変数列・目的関数の値・制約の値をわかりやすく表示でき、解析を行いやすくする。
- さらにdecodeされた結果から変数列の状態を抽出したい場合は`.solutions`、目的関数がほしい場合は`.objectives`、制約がどれくらい破れているかを確認したい場合は`.constraint_expr_value`と`.constraint_violations`を用いる。

JijModelingを用いれば、QUBO定式化された数式を簡単に実装することが可能です。またそれをJijZeptを用いることで、素早く求解することができます。

# 参考文献

[1] [Lucas, 2013, "Ising formulations of many NP problems"](https://www.frontiersin.org/articles/10.3389/fphy.2014.00005/full)  
[2] [Finn, 1973, "Integer Programming, Linear Programming and Capital Budgeting"](https://onlinelibrary.wiley.com/doi/10.1111/j.1467-6281.1973.tb00186.x)  
[3] [Floudas & Lin, 2005, "Mixed Integer Linear Programming in Process Scheduling: Modeling, Algorithms, and Applications"](https://link.springer.com/article/10.1007%2Fs10479-005-3446-x)  
[4] 梅谷俊治, "しっかり学ぶ数理最適化 -モデルからアルゴリズムまで-"